# Analysis of cooccurrences of frequent lemmatas

In this notebook, the cooccurrences of frequent lemmatas are analized in form of graphs.

[3 July 2023] This work has only just been sketched out, and needs to be developed further

In [55]:
import psycopg2
import pandas as pd
from importlib import reload
import seaborn as sns
from matplotlib import pyplot as plt
from itables import init_notebook_mode, show
import networkx as nx
import settings as stt
import pydot
from networkx.drawing.nx_pydot import graphviz_layout
import graphviz

In [2]:
conn = psycopg2.connect(host="localhost", port = 5432, database="espace_intellectuel", 
                        user="postgres", password=stt.dbw)

In [3]:
conn

<connection object at 0x7fc6dd811a80; dsn: 'user=postgres password=xxx dbname=espace_intellectuel host=localhost port=5432', closed: 0>

In [4]:
### Defines a generic SQL query function to execute SELECT queries
def sql_explore(q, cnn):
    """
    q : the SQL query as text
    cnn : the connection parameter
    """
    errors_list = []
    elem = []
    with cnn.cursor() as curs:
        try:   
            ### Décommenter pour nouvelle exécution
            curs.execute(q)
            elem = curs.fetchall()
            conn.commit()
        except Exception as e:
            errors_list.append(e)
    return [elem, errors_list]        

In [5]:
q ="""
select t_lemma, t_lemma_2, count(*) as eff 
from astronomers.cooccurrence_in_sentence
group by t_lemma, t_lemma_2
order by eff desc limit 500;
"""

In [6]:
result = sql_explore(q, conn)
print(f'Lines count: {len(result[0])}, errors count: {len(result[1])}, \nFirst lines: {result[0][:5]}')

Lines count: 500, errors count: 0, 
First lines: [('University', 'University', 3804), ('Academy', 'Sciences', 3589), ('theory', 'theory', 2945), ('publish', 'paper', 2794), ('Mathematical', 'Society', 2713)]


In [7]:
df = pd.DataFrame(result[0])
df.columns=['t1', 't2', 'freq']
df.head()

t1          t2  freq
0    University  University  3804
1       Academy    Sciences  3589
2        theory      theory  2945
3       publish       paper  2794
4  Mathematical     Society  2713

In [8]:
###
# https://networkx.org/documentation/stable/reference/generated/networkx.convert_matrix.from_pandas_edgelist.html
G = nx.from_pandas_edgelist(df, source = "t1", target = "t2", edge_attr=["freq"], create_using=nx.Graph)

In [25]:
### Principales caractéristiques de ce graphe

# MultiGraph: Undirected graphs with self loops and parallel edges
# https://networkx.org/documentation/stable/reference/classes/index.html

##  , G.is_directed()  , len(nx.recursive_simple_cycles(G))
G.is_multigraph(),nx.is_connected(G), G.number_of_nodes(), G.number_of_edges(), nx.density(G)


(False, False, 174, 420, 0.027905122583217062)

In [10]:
len(G.nodes)

174

In [30]:
len(list(nx.nodes_with_selfloops(G)))

0

In [29]:
### Éliminer les selfloops
G.remove_edges_from(nx.selfloop_edges(G))

In [31]:
components = nx.connected_components(G);
components_l = [len(c) for c in sorted(nx.connected_components(G), key=len, reverse=True)]
len(components_l), components_l[:5]

(12, [153, 3, 3, 3, 2])

In [32]:
lcc = [[list(c), len(c)] for c in components]; len(lcc)

12

In [38]:
len(lcc[0][0])

153

In [42]:
lcc[0][0][:3]

['daughter', 'topic', 'course']

In [40]:
lcc[2]

[['II', 'War', 'World'], 3]

In [41]:
#### La composante de dimension maximale
largest_cc = max(nx.connected_components(G), key=len)

In [14]:
list(largest_cc)[:3]

['daughter', 'topic', 'course']

In [43]:
SG = G.subgraph(largest_cc)

In [44]:
nx.is_connected(SG), SG.number_of_nodes(), SG.number_of_edges(), nx.density(SG)

(True, 153, 362, 0.031131750945992433)

In [50]:
import os

In [64]:
graph_path='/home/francesco/miniconda3/envs/cas_data_wrangling/bin/neato'
if not graph_path in os.environ["PATH"]: 
    os.environ["PATH"] += os.pathsep + graph_path

In [65]:
paths = os.environ["PATH"]
print(paths)


/home/francesco/miniconda3/envs/env_jupyterlab/bin:/home/francesco/miniconda3/condabin:/home/francesco/.local/bin:/usr/local/sbin:/usr/local/bin:/usr/sbin:/usr/bin:/sbin:/bin:/usr/games:/usr/local/games:/snap/bin:/home/francesco/miniconda3/envs/cas_data_wrangling/lib/graphviz:/home/francesco/miniconda3/envs/cas_data_wrangling/bin/neato


In [70]:
! neato -V

/bin/bash: neato: command not found


In [72]:
# https://networkx.org/documentation/stable/reference/drawing.html
plt.figure(figsize = (50,300))

#g = POG
g = SG

# https://stackoverflow.com/questions/57512155/how-to-draw-a-tree-more-beautifully-in-networkx

#pos = graphviz_layout(g)
pos = nx.kamada_kawai_layout(g)
### https://networkx.org/documentation/stable/reference/generated/networkx.drawing.layout.spring_layout.html
#pos = nx.spring_layout(g, k=2)

labels = {e: g.get_edge_data(e[0], e[1])["freq"] for e in g.edges()}

cp = 'grey'
nx.draw_networkx_nodes(g, pos, node_size=2, node_color=cp, alpha=0.8)
nx.draw_networkx_edges(g, pos, alpha=0.3) # edgelist=ln, edge_color=c, 
nx.draw_networkx_labels(g, pos, alpha=0.7, font_size=25)
nx.draw_networkx_edge_labels(g, pos=pos, edge_labels=labels)



plt.show()
